In [1]:
import librosa
import soundfile as sf
import os
import re
import numpy as np 
import argparse
import warnings
import torchaudio
import torch
from matplotlib import pyplot as plt
import IPython
import pickle
import torch_utils
from PIL import Image
from vscode_audio import Audio


In [240]:
#load infered image
im = Image.open('/home/bdh/thesis/training-runs/00007-images-auto1-noaug/fakes001400.png')

In [ ]:
max = 100
sr = 44100

runs = ['fakes000000','fakes000200','fakes000400','fakes000600','fakes000800','fakes001000','fakes001200','fakes001400','fakes001600','reals']

for run in runs:
	for i in range(5):
		for j in range(2):
			im = Image.open('/home/bdh/thesis/training-runs/00009-images-mixsets-auto1-noaug/{}.png'.format(run))
			# Inverse preprocessing:
			S = np.asarray(im)
			S = np.mean(S[513*i:513*(i+1),513*j:513*(j+1)], axis =2)
			S = np.float32(S/255)
			S = S*max

			# Invert using Griffin-Lim
			y_inv = librosa.griffinlim(S,n_iter=100, win_length=1024, hop_length=512 )
			y_inv = np.repeat(y_inv[np.newaxis,:],2, axis=0)
			y_inv = y_inv[:,0:162830]
			y_inv = torch.from_numpy(y_inv)
		
			torchaudio.save('/home/bdh/thesis/909/data/test/07-03-2022/{}-{}.wav'.format(run,i+j), y_inv, sr)
			break
Audio(y_inv, sr)

In [ ]:
import os
import sys

#save the literal filepath to both directories as strings
tu_path = os.path.join('/home/bdh/thesis/','stylegan2-ada-pytorch','torch_utils')
dnnlib_path = os.path.join('/home/bdh/thesis/','stylegan2-ada-pytorch','dnnlib')

#add those strings to python path
sys.path.append(tu_path)
sys.path.append(dnnlib_path )

In [2]:
with open('/home/bdh/thesis/training-runs/00009-images-mixsets-auto1-noaug/network-snapshot-001000.pkl', 'rb') as f:
    G = pickle.load(f)['G_ema'].cuda()  # torch.nn.Module
z = torch.randn([1, G.z_dim]).cuda()    # latent codes
c = None                                # class labels (not used in this example)
img = G(z, c)
print(img.shape)

Setting up PyTorch plugin "bias_act_plugin"... Done.
Setting up PyTorch plugin "upfirdn2d_plugin"... Done.
torch.Size([1, 3, 512, 512])


In [6]:
griffinlim = torchaudio.transforms.GriffinLim(n_iter=100,n_fft = 1024, hop_length=512).cuda()


In [9]:
sr = 44100
z = torch.randn([1, G.z_dim]).cuda()    # latent codes
c = None                                # class labels (not used in this example)
img = G(z, c)
img = torch.transpose(img,0,2)
img = torch.transpose(img,1,3)
img = torch.transpose(img, 2,3)
img = torch.mean(img, dim=2)
img = torch.squeeze(img)

const = torch.ones(513,1).cuda()*0.01
S = torch.cat([torch.unsqueeze(torch.mean(img,0),0),img], dim=0)
S = torch.cat([S,const], dim=1)
S.unsqueeze(dim=2)

#scale between 0 and 1
S -= S.min()
S /= S.max()

X = griffinlim(S)
Audio(X, sr)


tensor([[0.0593, 0.0405, 0.0429,  ..., 0.0441, 0.0465, 0.6123],
        [0.3137, 0.1894, 0.1648,  ..., 0.0585, 0.1095, 0.6123],
        [0.5950, 0.4523, 0.4266,  ..., 0.0374, 0.0658, 0.6123],
        ...,
        [0.0667, 0.0425, 0.0488,  ..., 0.0626, 0.0800, 0.6123],
        [0.0727, 0.0420, 0.0459,  ..., 0.0693, 0.1094, 0.6123],
        [0.1493, 0.0924, 0.0775,  ..., 0.1378, 0.1695, 0.6123]],
       device='cuda:0')

In [320]:

torch.randn([1, G.z_dim]).cuda()

tensor([[-1.1682e+00,  1.4897e+00,  1.3573e-01, -1.6288e+00,  1.4155e+00,
         -9.6377e-01, -9.8494e-01, -2.2995e-01,  7.3662e-01,  1.4806e+00,
         -4.0968e-01, -8.4318e-01, -9.7657e-01, -4.4769e-01, -2.2865e-01,
          1.4445e+00, -8.2997e-01, -8.3860e-01,  6.9388e-02,  4.1152e-01,
          4.1805e-01,  1.3357e+00, -4.0256e-01, -1.2533e-01,  1.4715e+00,
         -3.3885e-01, -4.3691e-01, -3.6872e-01,  3.0535e-01,  3.2864e-01,
          5.1595e-01, -4.2938e-01,  4.7653e-01, -1.7921e+00, -5.4189e-01,
          1.0399e+00, -1.8709e-01, -3.7027e-01, -6.0244e-01, -4.7446e-01,
          1.5806e+00,  2.8415e-01, -1.7561e+00,  9.0429e-01, -1.9757e-01,
          2.4127e-01,  1.3462e+00,  1.4577e-01, -7.5185e-02, -2.9157e-01,
         -4.6414e-01,  5.8533e-01, -9.4397e-02,  3.3629e-01, -1.9107e+00,
          7.5833e-01, -1.4459e+00, -3.6446e-01, -1.7168e+00, -2.8083e-03,
         -1.2978e+00,  2.4159e-01, -6.0856e-01, -4.1152e-01,  1.4601e+00,
         -2.2772e+00, -1.5549e+00,  1.

In [282]:

const = torch.ones(3,1).cuda()*0.01
const.device

device(type='cuda', index=0)

In [283]:

const = torch.ones(513,1).cuda()*0.01
S_ = torch.cat([torch.unsqueeze(torch.mean(img,0),0),img], dim=0)
S_ = torch.cat([S_,const], dim=1)
S_.unsqueeze(dim=2)
S_.shape

torch.Size([513, 513])

In [ ]:
griffinlim = torchaudio.transforms.GriffinLim(n_iter=100, win_length=1024, hop_length=512).cuda()

In [ ]:

# Inverse preprocessing:
S = np.asarray(img)
S = np.mean(S[0:513*2,0:513*2], axis =2)
S = np.float32(S/255)
S = de_normalize(S, max)

# Invert using Griffin-Lim
y_inv = librosa.griffinlim(S,n_iter=100, win_length=1024, hop_length=512 )
y_inv = np.repeat(y_inv[np.newaxis,:],2, axis=0)
y_inv = torch.from_numpy(y_inv)

torchaudio.save('/home/bdh/thesis/909/data/test/b.wav', y_inv, sr)
print(sr)
Audio(y_inv, sr)

TypeError: can't convert cuda:0 device type tensor to numpy. Use Tensor.cpu() to copy the tensor to host memory first.

In [273]:
y, sr = librosa.load(librosa.ex('trumpet'))

S = np.abs(librosa.stft(y[0:2],n_fft=4))
S=S[1:, :-1]
S= torch.tensor(S)

#add mean frequency to top
#add constant frequency

const = torch.ones(3,1)*0.01
S_ = torch.cat([torch.unsqueeze(torch.mean(S,0),0),S], dim=0)
S_ = torch.cat([S_,const], dim=1)
S_.unsqueeze(dim=2)
S_.shape

torch.Size([3, 3])